In [2]:
# === Install required packages ===
!pip install --quiet pandas openpyxl statsmodels

# === Imports ===
import pandas as pd
import numpy as np
import statsmodels.api as sm
from statsmodels.stats.outliers_influence import variance_inflation_factor

# === Load datasets ===
controls = pd.read_excel('/content/Controls.xlsx')
core = pd.read_excel('/content/Core.xlsx')
institutional = pd.read_excel('/content/Institutional.xlsx')

# === Merge and clean ===
df = pd.concat([controls, core, institutional], axis=1)
df = df.loc[:, ~df.columns.duplicated()]  # Drop duplicate columns

# Drop identifiers and friend1-3
drop_cols = ['id_', 'friend1', 'friend2', 'friend3']
df = df.drop(columns=[col for col in drop_cols if col in df.columns], errors='ignore')

# Ensure numeric
df = df.apply(pd.to_numeric, errors='coerce')

# Remove zero or missing income before log
df = df[df['income'] > 0]
df['log_income'] = np.log(df['income'])

# Select relevant variables
relevant_vars = [
    'log_income', 'trust', 'fair', 'helpful', 'helpfrds', 'socfrend',
    'confed', 'conjudge', 'conlegis', 'confedvacy', 'confedvac', 'confedy',
    'age', 'educ', 'sex', 'race', 'polviews', 'polint', 'relig'
]
df = df[[var for var in relevant_vars if var in df.columns]].dropna()

# === Define X and y ===
y = df['log_income']
X = df.drop(columns=['log_income'])
X = sm.add_constant(X)

# === Variance Inflation Factor (VIF) ===
vif_data = pd.DataFrame()
vif_data["feature"] = X.columns
vif_data["VIF"] = [variance_inflation_factor(X.values, i) for i in range(X.shape[1])]

print("\n=== VIF CHECK ===")
print(vif_data.sort_values("VIF", ascending=False))

# === OLS with robust standard errors (HC3) ===
model_robust = sm.OLS(y, X).fit(cov_type='HC3')
print("\n=== OLS Regression with Robust SEs (HC3) ===")
print(model_robust.summary())

# === OLS with clustered standard errors by 'sex' ===
cluster_var = df['sex']  # You can change this to another grouping variable if available
model_clustered = sm.OLS(y, X).fit(cov_type='cluster', cov_kwds={'groups': cluster_var})
print("\n=== OLS Regression with Clustered SEs (by sex) ===")
print(model_clustered.summary())

# === OPTIONAL: Logistic regression with high-income dummy ===
# Create binary outcome
df['high_income'] = (df['income'] > df['income'].median()).astype(int)
y_logit = df['high_income']
X_logit = sm.add_constant(df.drop(columns=['log_income', 'income', 'high_income']))

# Run logit model
logit_model = sm.Logit(y_logit, X_logit).fit()
print("\n=== Logistic Regression for High-Income Dummy ===")
print(logit_model.summary())



=== VIF CHECK ===
       feature        VIF
0        const  48.713048
2         fair   4.887950
8     conlegis   3.869113
7     conjudge   3.573634
1        trust   3.542135
3      helpful   3.518653
6       confed   3.396302
5     socfrend   1.103365
12         age   1.080870
13        educ   1.077666
17      polint   1.065318
16    polviews   1.050270
9   confedvacy   1.050172
11     confedy   1.043530
10   confedvac   1.034016
15        race   1.032080
14         sex   1.012707
4     helpfrds   1.012288
18       relig   1.008409

=== OLS Regression with Robust SEs (HC3) ===
                            OLS Regression Results                            
Dep. Variable:             log_income   R-squared:                       0.147
Model:                            OLS   Adj. R-squared:                  0.147
Method:                 Least Squares   F-statistic:                     512.2
Date:                Sun, 20 Jul 2025   Prob (F-statistic):               0.00
Time:               

/usr/local/lib/python3.11/dist-packages/statsmodels/base/model.py:1894: ValueWarning: covariance of constraints does not have full rank. The number of constraints is 18, but rank is 2
  warnings.warn('covariance of constraints does not have full '


KeyError: 'income'